![alt text](https://wiki.icecube.wisc.edu/images/a/a4/HESE75_skymap_with_events.png)

# Diffuse Neutrinos #

IceCube Bootcamp 2019 \\
Madison, WI 

*Ibrahim Safa &
Manuel Silva*

# Introduction and Goals #


*  Learn what diffuse neutrinos are and how IceCube actually detects them
*  Review of Poisson statistics and likelihood construction
*  Run your own diffuse fit using IceCube data


![alt text](https://www.researchgate.net/profile/J_Joutsenvaara/publication/304487324/figure/fig5/AS:492577876123650@1494451126031/Neutrino-energy-ranges-and-their-relative-intensities-according-to-their-source-of_W640.jpg)



# Summary of diffuse neutrino fluxes for all energy ranges. 

- Cosmological neutrinos are neutrinos left over from the Big Bang
- Solar neutrinos are byproducts of nuclear fusion reactions in the stellar core
- Atmospheric neutrinos are created when cosmic rays bombard our atmosphere
- Astrophysical neutrinos are created near cosmic accelarator sites alongside cosmic rays.
- GZK neutrinos are created when protons interact with the cosmic microwave background, very high energy, IceCube not optimized for this



# Diffuse Neutrinos #

*  Diffuse neutrinos are neutrinos that do not appear to be coming from any particular source (isotropic), they are the total neutrinos that eventually "hit" IceCube
*  As an experimentalist, you would analyze your data and test several models 
    *  Most IceCube diffuse fits publish the astrophysical spectral index $\gamma$ and overall normalization $\Phi_0$ where the flux is defined as: $ \Phi_0~ (\frac{E}{100TeV})^{-\gamma} $
    
    *  If your data sample has atmospheric neutrinos, you also fit this and extract agreement/disagreements with these models
    
*  Theorists would then use our fitted data to predict new models, optimize theirs, etc....

*  For reference, IceCube is capable of detecting both Atmospheric and Astrophysical Neutrinos, if you want high purity of one you would need an event selection to chose one over the other

# Observable - Energy #

*  The diffuse neutrino flux is highly dependent on energy, therefore we must have a good grasp for the energy of detected neutrinos
*  IceCube doesn't measure energy though, it measures light/charge deposited in each DOM
  * Use a reconstruction algorithim to convert the light into energy, [summary of published algorithims](https://arxiv.org/pdf/1311.4767.pdf)
*  This is our **first observable**

# Observable - Zenith #

*  Astrophysical neutrino flux depends slightly on zenith, however the atmospheric flux is higly dependent on zenith
*  The earth acts as a "shield" and filters out some of the neutrinos/muons that reach IceCube
  * This is due to the fact that depending on the direction, there is varying lengths of air/rock/ice that the particles must travel to eventually reach IceCube, the probability of interacting depends on energy
* You can use the light deposited in IceCube along with timing information, to predict the direction of the neutrinos
    *  Use a reconstruction algorithim to convert light and timing to direction, [summary of published algorithims](https://arxiv.org/pdf/astro-ph/0407044v1.pdf)
*  This is our **second observable**

# Observable - Zenith #

* Neutrinos need to traverse entire Earth for large zeniths, or through entire Ice for small zeniths

![alt text](https://icecube.wisc.edu/~msilva/BootCamp_2019/IceCube_zeniths.png)


# Observable - Flavor #
*  Neutrinos can interact with protons/neutrons in the ice via electroweak interaction
  *  Via neutral current (top) or weak current (bottom)
  *  Cannot extract information about the neutrino flavor from neutral currents, they all produce hadronic cascades
  *  Eletrons produce electromagnetic cascades, muons produce tracks,  taus produce a "double-bang"
  *  Note, it is very difficult to properly separate hadronic cascades from neutral current and electromagnetic cascades from electron-neutrinos, so for now lets group them together

  
![alt text](https://icecube.wisc.edu/~msilva/BootCamp_2019/Diagrams.png)

# Observable - Flavor #

![alt text](https://icecube.wisc.edu/~msilva/BootCamp_2019/EventTopologies.png)

# Observables - Summary #
*  For today's example, lets stick to using **energy, zenith, and topology as our observables **
*  Hopefully, you will be able to repurpose your code in the future if you ever need to add more/different observables

# Counting Statistics #

Consider a detector that counts particles. 

If our expectation of the rate (counts/s) is fixed over a given interval, and each count is independent of the previous or next one, the probability of seeing a count of **k** particles in your detector follows a poisson distribution.

The number of particles we detect in a time **t** is a random variable.

The probability, then, of getting **k** counts when expecting **$\lambda$** counts in time **t** is : 


$P(k | \lambda)=\frac{\lambda^{k} e^{-\lambda}}{k !}$




In [ ]:
#In code form
def poisson(k, l):
    return (l**k * np.exp(-l))/np.math.factorial(k)

In [ ]:
import numpy as np
from scipy import special
import matplotlib.pyplot as plt
%matplotlib inline

# Let's see what that looks like #

In [ ]:
l = range(1, 10)[::2]

for i in range(len(l)):
    probs  = [poisson(k, l[i]) for k in range(0,20)]
    plt.plot(range(0,20), probs, label='$\\lambda$ = {}'.format(l[i]))

plt.xlabel('Counts')
plt.ylabel('Probability')
plt.title('Poisson Distribution')
plt.legend()
plt.show()

# Ok Great, but how is this useful? #

In **reality**, what you have is a *detected* number of events, and you often try to estimate the *true* expectation.

Or, in math terms, the likelihood of $\lambda$-expected events given k-detected events is: 

$\Large \mathcal{L}(\lambda | k) =   P(k | \lambda)=\frac{\lambda^{k} e^{-\lambda}}{k !}$


Given that you have already seen **k** events in your detector, then we can estimate the true expectation with whatever value **maximizes** the probability that you will detect that many events.





# Now let's fit some toy data # 


- To do this, you'll need to load this file: **toy_data_E-2.npy**

    1) Download from: https://icecube.wisc.edu/~msilva/BootCamp_2019/toy_data_E-2.npy

- We are going to make some assumptions: 

    1) We have a spherical detector hovering in vacuum somehwere in deep space.
    
    2) Our detector is perfect (Reconstruction/Systematics etc.)
        
    3) We have prior knowledge of the incoming flux which is, conveniently, a simple power law defined as:   $ \large~~\Phi_0~ E^{-\gamma}$ 
    
    *where gamma is the spectral index, and it's known in this case to be ($\gamma$ = 2)
    
    4) We have been taking data continuously for ~100 years.
    
    
- Our goal is to fit for the normalization $\Phi_0$

In [ ]:
data = np.load('/Users/isafa/Downloads/toy_data_E-2.npy')

bins = np.logspace(3, 6, 10)
centers = (bins[1:] + bins[:-1])/2.
h = np.histogram(data, bins=bins)
plt.step(centers, h[0], where='mid', label='data')
plt.semilogy(nonposy='clip')
plt.semilogx()
plt.xlabel('Energy (GeV)')
plt.ylabel('Counts')
plt.legend()
plt.show()

- Now that we have our data, we can define the likelihood function, $\mathcal{L}$ :


$ \Large \mathcal{L}(\vec{\theta} | \vec{d})=\prod_{i} \frac{\left(\lambda_{i}\right)^{k_{i}} e^{-\lambda_{i}}}{k_{i} !}$


The only difference between the likelihood and the probability we defined earlier is that now you're taking into account that you have several bins. So you have an expectation $\lambda_{i}$ and an observed value $k_{i}$ in every bin "$i$" 

It's often easier for technical reasons to work with the negative log-likelihood function, which is just  - log($\mathcal{L}$): 

$ \Large \log \mathcal{L}(\theta | \vec{d})=\sum_{i} k_{i} \cdot \log \left(\lambda_{i}\right)-\lambda_{i}-\Gamma\left[k_{i}+1\right]$


We want to maximize the probability that a certain expectation gives us the observed dataset. So we can maximize log($\mathcal{L}$)  (or minimize negative log($\mathcal{L}$))

We will now define a function that returns our expectation in a certain bin, and another one that evaluates the likelihood.

The **expectation** or number of events
in a bin i is:

$ \Large \lambda_i$ = $\Phi_0~ \int_{E_i} \frac{dN}{dE} dE$

In [ ]:
years = 365.*86400. #seconds
livetime = 100.*years
effA = 1e4 #cm^2 (cross-section of interaction * number of targets)

def expectation(phi_0, i):
    return phi_0*(1./(bins[i]) - 1./(bins[i+1]))*livetime*effA

#We are given the spectral index, so our only free parameter in this case is the normalization $\Phi_0$
def log_likelihood(data, phi_0):
    llh = []
    for i in range(len(data)):
        llh.append(-(data[i] * np.log(expectation(phi_0, i)) - expectation(phi_0, i) - special.loggamma(data[i]+1)))

    llh = np.sum(np.asarray(llh)).real
    return llh

# We have a likelihood! # 

There are two ways to minimize it.

1) The easy way is to scan your likelihood function and pick out the minimum. 
This can get computationally intensive and practically impossible for large datasets / many free parameters.

2) The harder/better way is to use a *minimizer*. Minimizers are special algorithms developed specifically to find the minima of a given function across an arbitrary number of dimensions.

# We'll start by scanning our likelihood #

In [ ]:
phis = np.logspace(-8, -4, 50)
profile = [log_likelihood(h[0], phi) for phi in phis]
plt.plot(phis, profile)
plt.xlabel('$\Phi_0$ [GeV$^{-1}$ cm$^{-2}$ s$^{-1}$ sr$^{-1}$]')
plt.ylabel('$ - \ell \ell h$ value', fontsize=16)
plt.loglog()

In [ ]:
norm_scanned = phis[np.where(profile == min(profile))[0][0]]

# Now let's use a minimizer #

In [ ]:
import scipy.optimize as sp

In [ ]:
res = sp.minimize(lambda x: log_likelihood(h[0], *x),
                           [3.e-7],
                           method='L-BFGS-B',
                           bounds=[[0,None]])

print(res)
norm_min = res.x[0]

In [ ]:
print('Percent difference between minmizer and scanned value: {}'.format((norm_min - norm_scanned)/(norm_min) * 100.))

The scanned value was within ~10 percent of the minimized value. Not bad!
The accuracy of the scanned value increases with the number of points sampled, so for physics analyses with lots of dimensions to scan over, the number of points needed will become unmanageable.

# Now we can plot our fitted function against the data#

In [ ]:
def power_law(norm, E):
  return norm*E**(-2)


bins = np.logspace(3, 6, 10)
centers = (bins[1:] + bins[:-1])/2.
lower = centers - bins[:-1] 
upper = bins[1:] - centers
xerr = np.array([lower, upper])

norm = norm_min
dats = [expectation(norm_min, i) for i in range(len(centers))]

plt.figure(figsize=[8,5])
plt.step(bins, np.asarray(dats + [0]), where='post',linewidth=2, label='fit')
plt.errorbar(centers, h[0], xerr=xerr, yerr=(np.sqrt(h[0])),capsize=4,fmt='o',color='k',alpha=0.9,label='data',linewidth=2)
plt.semilogy(nonposy='clip')
plt.semilogx()
plt.legend(fontsize=15, loc='lower left', fancybox = True)
plt.grid(ls='-.',which='both',alpha=0.3)
plt.xlabel('Energy (GeV)',fontsize=15)
plt.ylabel('Number of Events', fontsize=15)
plt.text(3e4, 3e3, 'BOOTCAMP PRELIMINARY', fontsize=16, color='red')
plt.show()